## Visualizing results
This notebook is meant to be run after script_cnm

### Import packages

In [ ]:
# importing packages/modules
from decode_lab_code.preprocessing.ophys.caiman_wrapper import caiman_preprocess

import matplotlib.pyplot as plt

import numpy as np

import caiman as cm
from caiman.source_extraction import cnmf
from caiman.utils.utils import download_demo
from caiman.utils.visualization import inspect_correlation_pnr, nb_inspect_correlation_pnr, display_animation
from caiman.motion_correction import MotionCorrect
from caiman.source_extraction.cnmf import params as params
from caiman.utils.visualization import plot_contours, nb_view_patches, nb_plot_contour
import cv2

try:
    cv2.setNumThreads(0)
except:
    pass
import bokeh.plotting as bpl
import holoviews as hv
bpl.output_notebook()

try:
    hv.notebook_extension('bokeh')
except:
    print("fail")

import copy

from matplotlib import animation

import glob

### Load in results from cnm

In [13]:
# assign folder name and file name
folder_name = '/Users/js0403/ophysdata/Akanksha_data/'
file_name = 'Movie_23'

# search for files matching file_name
pathnames = glob.glob(folder_name+file_name+'*')
pathnames.sort()

# assigned file names
file_name_mmap = [i for i in pathnames if 'memmap' in i][0]
file_name_cnm = [i for i in pathnames if 'cnm' in i][0]
cnm = cnmf.cnmf.load_CNMF(filename=file_name_cnm, n_processes=1, dview=None)

# load the image data
Yr, dims, T = cm.load_memmap(file_name_mmap)
images = np.reshape(Yr.T, [T] + list(dims), order='F') 

Decode mmap filename /Users/js0403/ophysdata/Akanksha_data/Movie_23_memmap_d1_256_d2_384_d3_1_order_C_frames_2832.mmap


In [11]:
file_name_cnm

'/Users/js0403/ophysdata/Akanksha_data/Movie_23_cnm.hdf5'

In [14]:
# run summary image
cn_filter, pnr = cm.summary_images.correlation_pnr(
    images, gSig=cnm.params.init.get('gSig')[0],center_psf=True,swap_dim=False) # change swap dim if output looks weird, it is a problem with tiffile

### Removed background

In [15]:
# remove background and extract output
include_background = False

# Watch the video without the background in order to confirm results
mov = cnm.estimates.play_movie(images, q_max=99.9, magnification=1,
                                 include_bck=include_background, gain_res=2, bpx=0)

### Play another way

In [16]:
adjShape = int(mov.shape[2]/3)
# extract the reconstructed video 
mov_nobck = mov[:,:,0:adjShape]
mov_recon = mov[:,:,adjShape+1:adjShape*2+1]
mov_recon.play()

### Filtered

In [18]:
try:
    c, dview, n_processes = cm.cluster.setup_cluster(
    backend='local', n_processes=None, single_thread=False)
except:
    cm.stop_server(dview=dview)
    c, dview, n_processes = cm.cluster.setup_cluster(
        backend='local', n_processes=None, single_thread=False)

In [19]:
min_SNR = 3            # adaptive way to set threshold on the transient size
r_values_min = 0.9     # threshold on space consistency (if you lower more components
#                        will be accepted, potentially with worst quality)
cnm.params.set('quality', {'min_SNR': min_SNR,
                           'rval_thr': r_values_min,
                           'use_cnn': False})

# component evaluation
cnm.estimates.evaluate_components(images, cnm.params, dview=dview)

print(' ***** ')
print('Number of total components: ', len(cnm.estimates.C))
print('Number of accepted components: ', len(cnm.estimates.idx_components))


Decode mmap filename /Users/js0403/ophysdata/Akanksha_data/Movie_23_memmap_d1_256_d2_384_d3_1_order_C_frames_2832.mmap
Decode mmap filename /Users/js0403/ophysdata/Akanksha_data/Movie_23_memmap_d1_256_d2_384_d3_1_order_C_frames_2832.mmap


 ***** 
Number of total components:  89
Number of accepted components:  39


### Get df/f

In [22]:

# get df/f
#cnm.estimates.detrend_df_f(quantileMin=8, frames_window=500, flag_auto=True)
cnm.estimates.detrend_df_f(flag_auto=False, detrend_only=True)

# lets get the dF/F
dfF_all = cnm.estimates.F_dff

# get only good components
dfF_good = dfF_all[cnm.estimates.idx_components]

# get total time
totalTime = dfF_good.shape[1]/15

# make x-axis
xAxis = np.linspace(0,totalTime,dfF_good.shape[1])

"""
fig = plt.figure(dpi=2000)
ax = fig.add_subplot(dfF_good.shape[0],projection='3d')
ax.set_xlabel('Time (sec)')
ax.set_ylabel('norm. dF/F')
ax.axis('off')
for i in range(dfF_good.shape[0]):
    line = ax.plot()
"""

fig = plt.figure(dpi=2000)
gs  = fig.add_gridspec(dfF_good.shape[0], hspace=0)
axs = gs.subplots(sharex=True, sharey=False)

range(dfF_good.shape[0])
for i in range(dfF_good.shape[0]):
    axs[i].plot(xAxis,dfF_good[i,:],'k',linewidth=0.5)
    axs[i].set_yticks([])
    #axs[i].xticks(fontsize=8)       
    if i != dfF_good.shape[0]-1:   
        axs[i].axis('off')
    else:
        axs[i].set_frame_on(False)